In [1]:
import seaborn as sns
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import ds_tools as dst
from statsmodels.api import tsa
from plotly.subplots import make_subplots
import glob

## *Loading Data*

The dataset used for this project is very large (~8GB). In order to read the `.csv` without exceeding the memory available, a `chunksize` parameter has been defined. This allows the file to be read in chunks of 1,000,000 rows, thus reducing RAM usage.

In [5]:
LCL = pd.DataFrame()                                    # Instantiate a DataFrame
LCL_chunk = pd.read_csv('data/raw/CC_LCL-FullData.csv', # Read .csv file
                        parse_dates=[2],                # Read in column 2 as datetime object
                        infer_datetime_format=True, 
                        chunksize= 1000000,             # Read in chunks of 1,000,000 rows
                        low_memory=False,
                        na_values='Null',               # Set 'Null' strings in the dataset as null values
                        verbose=2,)
while True:
    try:
        LCL = pd.concat([LCL, next(LCL_chunk)], ignore_index=True)      # Add rows to DataFrame
    except:
        break

Tokenization took: 2362.94 ms
Type conversion took: 496.13 ms
Parser memory cleanup took: 27.93 ms
Tokenization took: 1321.32 ms
Type conversion took: 726.21 ms
Parser memory cleanup took: 25.10 ms
Tokenization took: 1472.31 ms
Type conversion took: 673.95 ms
Parser memory cleanup took: 31.25 ms
Tokenization took: 1048.10 ms
Type conversion took: 488.48 ms
Parser memory cleanup took: 42.88 ms
Tokenization took: 1349.86 ms
Type conversion took: 544.88 ms
Parser memory cleanup took: 39.11 ms
Tokenization took: 1122.64 ms
Type conversion took: 470.54 ms
Parser memory cleanup took: 21.35 ms
Tokenization took: 1509.82 ms
Type conversion took: 509.85 ms
Parser memory cleanup took: 50.86 ms
Tokenization took: 1159.34 ms
Type conversion took: 637.62 ms
Parser memory cleanup took: 31.05 ms
Tokenization took: 1284.88 ms
Type conversion took: 490.49 ms
Parser memory cleanup took: 29.64 ms
Tokenization took: 1008.89 ms
Type conversion took: 454.20 ms
Parser memory cleanup took: 23.05 ms
Tokenizati

In [58]:
# Load ACORN rating data
acorn = pd.read_csv('data/raw/household_info.csv')
acorn.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5566 entries, 0 to 5565
Data columns (total 5 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   LCLid          5566 non-null   object
 1   stdorToU       5566 non-null   object
 2   Acorn          5566 non-null   object
 3   Acorn_grouped  5566 non-null   object
 4   file           5566 non-null   object
dtypes: object(5)
memory usage: 217.5+ KB


In [2]:
# LCL_1 = pd.read_pickle('data/raw/LCL_1.pkl')
# LCL_2 = pd.read_pickle('data/raw/LCL_2.pkl')
# LCL = pd.concat([LCL_1, LCL_2])

In [5]:
# Check data types
LCL.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 165929555 entries, 21 to 167932473
Data columns (total 4 columns):
 #   Column                   Dtype         
---  ------                   -----         
 0   LCLid                    object        
 1   stdorToU                 object        
 2   DateTime                 datetime64[ns]
 3   KWH/hh (per half hour)   float32       
dtypes: datetime64[ns](1), float32(1), object(2)
memory usage: 5.6+ GB


Looking at the data types, we can see that there are two object columns which contain the household identifier, and the tariff. There is a datetime column which marks the half hourly interval where the data were recorded. Lastly, there is a float column, which provides the actual reading from the smart meter in KWH/hh

In [5]:
dst.basic_eda(LCL)

====================== BASIC EDA ======================        
Rows: 167932474        
Columns: 4        
Duplicates: 115453 rows, 0.07% of the DataFrame        
Nulls: 5560 null values in ['KWH/hh (per half hour) ']


Running some basic checks on the data, we can see that there are a number of duplicate rows. These rows are likely erroneous entries, as each household should only produce a single reading at each interval. The duplicate rows should therefore be dropped.

Null values may be left in the dataset as these will be ignored when the aggregation process is carried out

In [ ]:
LCL.head()

In [10]:

# LCL.drop_duplicates(inplace = True)

# LCL = LCL[LCL['KWH/hh (per half hour) '] != 0]

# LCL.set_index(LCL['DateTime'], inplace = True, drop = True)
# LCL.drop(columns = 'DateTime', inplace = True)

# LCL = LCL.join(acorn[['LCLid', 'Acorn_grouped']].set_index('LCLid'), on = 'LCLid') # Join Acorn affluence data


# # Rename columns
# LCL.rename(columns = {'stdorToU': 'tariff',
#                      'KWH/hh (per half hour) ':'KW',
#                      'Acorn_grouped': 'acorn'}, 
#                      inplace = True)

# LCL['KW'] = LCL['KW']*2

Looking at the ACORN categories, we can see that there two groups which appear uncategorised. These make up less than 1% of the data each. They may be dropped from the dataset.

In [14]:
LCL['acorn'].value_counts(normalize = True)

Affluent       0.403934
Adversity      0.326130
Comfortable    0.269936
Name: acorn, dtype: float64

In [11]:
to_keep = LCL.acorn.isin(['Affluent', 'Comfortable', 'Adversity'])
LCL = LCL[to_keep]

In [13]:
LCL['acorn'].value_counts(normalize = True)

Affluent       0.403934
Adversity      0.326130
Comfortable    0.269936
Name: acorn, dtype: float64

In [2]:
# # Checkpoint 

# LCL_Std = LCL[LCL_acorn['tariff'] == 'Std']
# LCL_ToU = LCL_acorn[LCL['tariff'] == 'ToU']

# LCL_Std.to_pickle('data/LCL_Std_a.pkl')
# LCL_ToU.to_pickle('data/LCL_ToU_a.pkl')

LCL_Std = pd.read_pickle('data/LCL_Std_a.pkl')
LCL_ToU = pd.read_pickle('data/LCL_ToU_a.pkl')
LCL = pd.concat([LCL_Std, LCL_ToU])

We can compare the proportions of each ACORN category present in the dataset to see if there is a significant difference between standard and variable tariffs.

In [21]:
LCL_Std['acorn'].value_counts(normalize = True)

Affluent       0.392203
Adversity      0.341456
Comfortable    0.266341
Name: acorn, dtype: float64

In [22]:
LCL_ToU['acorn'].value_counts(normalize = True)

Affluent       0.450522
Comfortable    0.284214
Adversity      0.265265
Name: acorn, dtype: float64

The proportion of households in the 'affluent' bracket is ~6% higher in the variable tariff sample than the standard tariff sample. This will inflate the variable tariff averages to an extent, however the effect is not expected to be significant as the difference is small.

We no longer require the household identifiers, as the remainder of the analysis will be done by aggregating the data by the time and tariff and calculating a mean value for each time-tariff combination.

In [3]:
LCL_Std.drop(columns='LCLid', inplace = True)
LCL_ToU.drop(columns='LCLid', inplace = True)

In [62]:
LCL = pd.concat([LCL_Std, LCL_ToU]) # Join back on to main DF

Now that we have only the data points we want, we can aggregate by the tariff and timestamp and calculate the mean power consumption of consumers on a fixed and variable tariff.

In [63]:
LCL = (LCL.groupby(['tariff', 'DateTime']).mean()).sort_values(by = ['tariff', 'DateTime']) # Find average for each datetime-tariff combination
LCL = LCL.unstack().T
LCL.index = LCL.index.get_level_values(1) # Get rid of multi-indexing
LCL.head()

tariff                  Std    ToU
DateTime                          
2011-11-23 09:00:00  0.7100  0.428
2011-11-23 09:30:00  0.8280  0.294
2011-11-23 10:00:00  0.3490  0.222
2011-11-23 10:30:00  0.2275  0.133
2011-11-23 11:00:00  0.2680  0.102

In [68]:
# Check for missing samples
first = LCL.index.min()
last = LCL.index.max()
full_range = pd.date_range(start = first, end = last, freq = '30T')
full_range.difference(LCL.index)

DatetimeIndex([], dtype='datetime64[ns]', freq=None)

In [60]:
# Checkpoint
# LCL.to_pickle('data/LCL_unstack.pkl')
LCL = pd.read_pickle('data/LCL_unstack.pkl')

Using the Date-Time index, we can resample at different frequencies to get a better understanding of how power consumption varies across tariffs at hourly, weekly, and monthly granularities.

We can do this by creating a helper function to resample at multiple frequencies.

In [65]:
def get_resamples (df, prds):
    '''
    Helper function to resample time series dataframe for multiple frequencies.

    ---INPUTS---
    df - Time series DataFrame with DateTime index
    prds - List of frequencies to resample e.g. ['H', 'W']

    ---OUTPUTS---
    resamples - List of resapled DataFrames
    
    '''
    resamples = []

    for prd in prds:
        resample = df.resample(prd).mean()
        resamples.append(resample)

    return resamples

In [66]:
[LCL_hrs, LCL_day, LCL_wks] = get_resamples(LCL, ['H', 'D', 'W'])

In [105]:
freqs = ['Hourly', "Daily", "Weekly"]
DFs = [LCL_hrs, LCL_day, LCL_wks]

fig = make_subplots(rows=3, cols=1, subplot_titles=freqs, shared_xaxes=False)

for i in range(len(freqs)):
    freq = freqs[i]
    df = DFs[i]

    fig.add_trace(
        go.Line(
            x=df.index, y=df['Std'], 
            name = 'Standard', 
            line_color = '#F2A74B',
            legendgroup = freq
            ),
        row = i+1,
        col = 1,
    )

    fig.add_trace(
        go.Line(
            x=df.index, y=df['ToU'], 
            name = 'Variable',
            line_color = '#415885',
            legendgroup = freq
            ),
        row = i+1,
        col = 1
    )

    fig.update_xaxes(title_text='Date-Time', row=i+1, col=1)
    fig.update_yaxes(title_text='Average Power (KW)', row=i+1, col=1)

    fig.update_layout(
        legend_title="Tariff", 
        title= "Power Usage of Different Tariffs Between 2011 and 2014",
        legend_tracegroupgap=350,
        height= 1200
    )

fig.show()

c:\Users\triha\anaconda3\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




Looking at the plots, it can be seen that there appears to be an anomaly at the start of the data, where the values for the variable tariff appears abnormally low. This could be due to faulty equipment during the setup of the data collection.

We will ignore readings before 2012 in order to discount these anomalies.

In [107]:
LCL = LCL[LCL.index >= '2012-01-01']                                # Ignore all values before 2012
[LCL_hrs, LCL_day, LCL_wks] = get_resamples(LCL, ['H', 'D', 'W'])   # Resample again

In [108]:
# Checkpoint
# LCL_hrs.to_pickle('data/LCL_unstack_hrs.pkl')
# LCL_day.to_pickle('data/LCL_unstack_day.pkl')
# LCL_wks.to_pickle('data/LCL_unstack_wks.pkl')

LCL_hrs = pd.read_pickle('data/LCL_unstack_hrs.pkl')
LCL_day = pd.read_pickle('data/LCL_unstack_day.pkl')
LCL_wks = pd.read_pickle('data/LCL_unstack_wks.pkl')

In [110]:
freqs = ['Hourly', "Daily", "Weekly"]
DFs = [LCL_hrs, LCL_day, LCL_wks]

fig = make_subplots(rows=3, cols=1, subplot_titles=freqs, shared_xaxes=False)

for i in range(len(freqs)):
    freq = freqs[i]
    df = DFs[i]

    fig.add_trace(
        go.Line(
            x=df.index, y=df['Std'], 
            name = 'Standard', 
            line_color = '#F2A74B',
            legendgroup = freq
            ),
        row = i+1,
        col = 1,
    )

    fig.add_trace(
        go.Line(
            x=df.index, y=df['ToU'], 
            name = 'Variable',
            line_color = '#415885',
            legendgroup = freq
            ),
        row = i+1,
        col = 1
    )

    fig.update_xaxes(title_text='Date-Time', row=i+1, col=1)
    fig.update_yaxes(title_text='Average Power (KW)', row=i+1, col=1)

    fig.update_layout(
        legend_title="Tariff", 
        title= "Power Usage of Different Tariffs Between 2012 and 2014",
        legend_tracegroupgap=350,
        height= 1200
    )

fig.show()

From the plots above it can be seen that there are clear trends in household power consumption. As expected, winter periods see the highest amount of power being consumed, whilst summer sees the lowest. 

We can also deduce that the series is multiplicative. There is clearly a greater variance in power consumption during the peak winter periods than there are during summer. This is likely due to the fact that people tend to spend more time indoors during winter. This means that alongside an increase in boiler use for heating, appliances which cause a relatively short spike in power consumption (e.g. kettles, microwaves) will be used more frequently, thus resulting in greater variability in the usage patterns.

What is surprising is that whilst those on a variable tariff use ~20-50W less than those on a standard tariff at any given time, the actual **patterns** of use are nearly identical. This is likely due to the fact that the changes in energy price do not occur at a fixed time, so not all households may reduce their consumption at the same time. Household occupants may for example be out of the home or asleep. This means that we are unlikely to see significant rises or falls during changes in energy price as the average consumption will be smoothed by the households not modifying their consumption over that particular period. However, the effect of the households reducing their consumption can be seen in the form of a lower average consumption, especially at larger granularities.

We can further compare the patterns of use for each tariff by taking an average date-time window (e.g. 1 day, 1 month, 1 year) and examining whether the difference changes significantly within this window.


In [119]:
# Find differences within time windows

# Average day, hourly frequency
hrs_diffs = LCL_hrs.groupby(LCL_hrs.index.hour).mean()
hrs_diffs['diffs'] = hrs_diffs['Std'] - hrs_diffs['ToU']

# Average month, daily frequency
day_diffs = LCL_day.groupby(LCL_day.index.day).mean()
day_diffs['diffs'] = day_diffs['Std'] - day_diffs['ToU']

#Average year, weekly frequency
wks_diffs = LCL_wks.groupby(LCL_wks.index.week).mean()
wks_diffs['diffs'] = wks_diffs['Std'] - wks_diffs['ToU']

C:\Users\triha\AppData\Local\Temp\ipykernel_9288\425846389.py:7: FutureWarning:

weekofyear and week have been deprecated, please use DatetimeIndex.isocalendar().week instead, which returns a Series. To exactly reproduce the behavior of week and weekofyear and return an Index, you may call pd.Int64Index(idx.isocalendar().week)



In [122]:
prds = ['Average Day', "Average Month", "Average Year"]
freqs = ['Hour', 'Day', 'Week']
DFs = [hrs_diffs, day_diffs, wks_diffs]

fig = make_subplots(rows=3, cols=1, subplot_titles=prds, shared_xaxes=False)

for i in range(len(prds)):
    prd = prds[i]
    df = DFs[i]
    freq = freqs[i]

    fig.add_trace(                          # Plot standard tariff
        go.Line(
            x=df.index, y=df['Std'], 
            name = 'Standard', 
            line_color = '#F2A74B',
            legendgroup = prd
            ),
        row = i+1,
        col = 1,
    )

    fig.add_trace(                          # Plot variable tariff
        go.Line(
            x=df.index, y=df['ToU'], 
            name = 'Variable',
            line_color = '#415885',
            legendgroup = prd
            ),
        row = i+1,
        col = 1
    )

    fig.add_trace(                          # Plot differences
        go.Line(
            x=df.index, y=df['diffs'], 
            name = 'Difference',
            line_color = '#363633',
            legendgroup = prd
            ),
        row = i+1,
        col = 1
    )

    fig.update_xaxes(title_text=freq, row=i+1, col=1)
    fig.update_yaxes(title_text='Average Power (KW)', row=i+1, col=1)

    fig.update_layout(
        legend_title = "Tariff", 
        title = "Power Usage Over Average Time Periods",
        legend_tracegroupgap=350,
        height= 1200
    )

fig.show()

c:\Users\triha\anaconda3\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




We can see from the average windows plotted above, the difference in power consumption between the two tariffs remains generally stable across all granularities. There is however, a small increase in the hourly difference on an average day at around 0000 hrs, gradually reducing to 0800 hrs. This could indicate a period where variable tariff households, who are more aware of their consumption, switch off unused appliances and chargers overnight to avoid an unactionable rise in price overnight.

In [123]:
wks_decomps = pd.DataFrame()
for col in LCL_wks.columns:
    name = col + '_Decomp'
    globals()[name] = tsa.seasonal_decompose(LCL_wks[[col]], model = 'multiplicative', period = 52, extrapolate_trend=True) # extrapolate_trend = 'freq' to fill in nulls
    wks_decomps[col + '_Trend'] = globals()[name].trend
    wks_decomps[col + '_Seasonal'] = globals()[name].seasonal
    wks_decomps[col + '_Residual'] = globals()[name].resid

In [43]:
wks_decomps.head()

Std_Trend  Std_Seasonal  Std_Residual  ToU_Trend  ToU_Seasonal  \
DateTime                                                                     
2012-01-01   0.449226      1.195208      0.975324   0.446963      1.203580   
2012-01-02   0.449192      1.216424      0.978907   0.446792      1.226320   
2012-01-03   0.449158      1.183942      1.008118   0.446621      1.199840   
2012-01-04   0.449124      1.174264      1.018612   0.446450      1.180259   
2012-01-05   0.449090      1.194312      1.009868   0.446279      1.202825   

            ToU_Residual  
DateTime                  
2012-01-01      0.983051  
2012-01-02      0.991809  
2012-01-03      1.034878  
2012-01-04      1.025812  
2012-01-05      0.993767

In [52]:
fig = px.line(x = wks_decomps.index, y = wks_decomps.Std_Trend)
fig.update_xaxes(rangeslider_visible=True)

In [53]:
fig = px.line(x = wks_decomps.index, y = wks_decomps.Std_Seasonal)
fig.update_xaxes(rangeslider_visible=True)

In [54]:
fig = px.line(x = wks_decomps.index, y = wks_decomps.Std_Residual)
fig.update_xaxes(rangeslider_visible=True)

In [93]:
X_Std_day = Std_day_df['7d_avg']
X_Std_day.dropna(inplace=True)

In [92]:
nans_idx = X_Std_day[X_Std_day.isna()].index

In [97]:
y_Std_day = Std_day_df['KW'].drop(nans_idx)


In [113]:
X_Std_day = pd.DataFrame(X_Std_day)

In [115]:
y_Std_day = pd.DataFrame(y_Std_day)

In [116]:
from sklearn.linear_model import LinearRegression
lin_Std_day = LinearRegression()
lin_Std_day.fit(X_Std_day, y_Std_day)
lin_Std_day.score(X_Std_day, y_Std_day)

0.9540566584943696

- Fill NAs
- Moving avg
- Decompose
- Compare variance at different intervals